In [ ]:
import socket
import struct
import pickle
import cv2
import torch
from ultralytics import YOLO
import time

In [ ]:

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
model = torch.hub.load('ultralytics/yolov5', 'yolov5n', pretrained=True)
model.to(device).eval()

model.conf = 0.35  # Set confidence threshold
model.iou = 0.25  #Set IoU threshold   

fps = 0

In [ ]:
def draw_boxes(img, results):
    det = results.xyxy[0].cpu()
    names = model.names
    for *xyxy, conf, cls in det.tolist():
        x1, y1, x2, y2 = map(int, xyxy)
        label = f"{names[int(cls)]} {conf:.2f}"
        cv2.rectangle(img, (x1, y1), (x2, y2), (0,255,0), 2)
        cv2.putText(img, label, (x1, y1 - 5),
                    cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0,255,0), 2)
        cv2.putText(img, f"FPS: {fps:.2f}", (20, 40),
                cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)
    return img

In [ ]:
HOST, PORT = "0.0.0.0", 7777
sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
sock.bind((HOST, PORT))
sock.listen(5)
print(f"Server listening on {HOST}:{PORT}...")

conn, addr = sock.accept()
print("Connected by", addr)

In [ ]:
data = b""
payload_size = struct.calcsize(">L")
prev_time = time.time()

In [ ]:
while True:
    # Receive message size
    start = time.time()

    while len(data) < payload_size:
        packet = conn.recv(4096)
        if not packet:
            break
        data += packet
    if not data:
        break

    packed_msg_size = data[:payload_size]
    data = data[payload_size:]
    msg_size = struct.unpack(">L", packed_msg_size)[0]

    # Receive frame data
    while len(data) < msg_size:
        data += conn.recv(4096)
    frame_data = data[:msg_size]
    data = data[msg_size:]

    # Deserialize
    frame = pickle.loads(frame_data)
    frame = cv2.imdecode(frame, cv2.IMREAD_COLOR)
    stop = time.time() - start

    # YOLO inference
    results = model(frame)
    # 🔹 Calculate FPS
    current_time = time.time()
    fps = 1 / (current_time - prev_time - stop)
    prev_time = current_time


    annotated = draw_boxes(frame, results)

        # Encode back to JPEG
    _, buffer = cv2.imencode(".jpg", annotated)
    msg = pickle.dumps(buffer, protocol=pickle.HIGHEST_PROTOCOL)
    msg = struct.pack(">L", len(msg)) + msg
    conn.sendall(msg)
conn.close()
